# Django login form

In [1]:
%load_ext restmagic
%rest_root http://mezzanine.jupo.org

Requests defaults are set.


## First attempt to login

In [2]:
%%rest --extract //p/text()
POST /en/admin/login/?next=/en/admin/
Content-Type: application/x-www-form-urlencoded

username=demo&password=demo

{
  "/html/body/div[1]/p[1]": "CSRF verification failed. Request aborted.",
  "/html/body/div[1]/p[2]": "You are seeing this message because this site requires a CSRF cookie when submitting forms. This cookie is required for security reasons, to ensure that your browser is not being hijacked by third parties.",
  "/html/body/div[1]/p[3]": "If you have configured your browser to disable cookies, please re-enable them, at least for this site, or for 'same-origin' requests."
}

<Response [403]>

### Enable cookies

In [3]:
%rest_session

New session started.


### Get the login page, this will set session CSRF cookie

In [4]:
r = %rest -q /en/admin/login/

### Still can't login, need a CSRF token

In [5]:
%%rest --extract //p/text()
POST /en/admin/login/?next=/en/admin/
Content-Type: application/x-www-form-urlencoded

username=demo&password=demo

{
  "/html/body/div[1]/p": "CSRF verification failed. Request aborted."
}

<Response [403]>

### CSRF token can be obtained from the cookie

In [6]:
token = r.cookies['csrftoken']
token

'63doppBRqzIxu1IQv5oNSnkTdlYRfweb7eWTPGbaeDVRjjpwh39IiHJq6s4tVaTo'

### Login success

In [7]:
%%rest -q
POST /en/admin/login/?next=/en/admin
Content-Type: application/x-www-form-urlencoded

username=demo&password=demo&csrfmiddlewaretoken=$token

<Response [200]>

### 'csrfmiddlewaretoken' field
CSRF token is also available in the hidden HTML form field:

In [8]:
%rest -e "//input[@name='csrfmiddlewaretoken']/@value" /en/admin/login/

{
  "/html/body/div/div[4]/div[1]/div[1]/form/input": "zhWj8iiRqsN0aCxsxrc5TGvNZEus3MzQG4HpR3w0RiZfvcrjTqSBPayc4aqjtWR0"
}

<Response [200]>